In [19]:
###This file is a demonstration of EHMM1 (https://doi.org/10.1016/j.aim.2025.110411) by Allen, Grove, Long and Tu
#### Running the first cell will precompute a few Hauptmodln as in Table 1 of EHMM1
#### A few demonstrations are provided
#### All equations and theorems labels are from the final version of EHMM
#### The current version date 7/9/25

def fr(a): #fractional part of a
    return a-floor(a)
####
def ris(a,k): #rising factorial
    return prod(a+i for i in srange(k))
####
def Hyp(A,B,x,N):
    return sum(prod(ris(a,i) for a in A)/prod(ris(a,i) for a in B)*x^i for i in srange(N))
####

q=var('q')
N=100 ###################     N=100, can adjust this number to get more coefficients
R.<q>=PowerSeriesRing(QQ,N)
def eta(m): #note that leading term q^(1/24) is not included
    return prod((1-q^(m*n)) for n in srange(1,N))
##A list of Hauptmodln from EHMM, HauptTable pairs these with corresponding hypergeometric data
HauptTable=[]
t2=16*q*eta(1)^8*eta(4)^(16)/eta(2)^(24) #t_2 of Table 1, namely modular lambda (2\tau)
HauptTable.append([[[1/2,1/2],[1,1]],t2])
uu=-64*q*eta(2)^(24)/eta(1)^(24)  #u for \Gamma_0(2) in Table 1
HauptTable.append([[[1/2,1/2,1/2],[1,1,1]],uu])
t4=uu/(uu-1) #page 53, $t_4$ for \Gamma_0(2) 
HauptTable.append([[[1/4,3/4],[1,1]],t4])
t3=27*q*eta(3)^(12)/(eta(1)^(12)+27*q*eta(3)^(12)) #page 53, $t_3$ for \Gamma_0(3)
HauptTable.append([[[1/3,2/3],[1,1]],t3])
t6p=108*q*eta(1)^(12)*eta(3)^(12)/(eta(1)^(12)+27*q*eta(3)^(12))^2    #from Table 1 of EHMM 1 t_{6+}
HauptTable.append([[[1/2,1/3,2/3],[1,1,1]],t6p])
t4p=256*q*eta(1)^(24)*eta(2)^(24)/(eta(1)^(24)+64*q*eta(2)^(24))^2  #from Table 1 of EHMM 1 t_{4+}
HauptTable.append([[[1/2,1/4,3/4],[1,1,1]],t4p])
t6a=t6p/(t6p-1)  #swap 1 and infinity for t6p
Jinv=1728/j_invariant_qexp(N) #1728/j-invariant
HauptTable.append([[[1/2,1/6,5/6],[1,1,1]],Jinv])
t6=(-(1-Jinv)^(1/2)/2+1/2) # $t_6$, 4 lines above Proposition 7.1
HauptTable.append([[[1/6,5/6],[1,1]],t6])
HauptTable.append([[[1/3,1/3],[1,1]],t3/(t3-1)]) #related to [1/3,2/3],[1,1] by Pfaff transformation
HauptTable.append([[[2/3,2/3],[1,1]],t3/(t3-1)]) #related to [1/3,2/3],[1,1] by Pfaff transformation
HauptTable.append([[[1/12,5/12],[1,1]],Jinv])
HauptTable.append([[[1/2],[1]],t2]) 
####comment out the following to space computation time and memory, remove # to use
###########
##Weight 1/2 Jacobi theta
###########
#T3=sum(q^(n^2) for n in srange(-11,11)) #\theta_3
#T4=sum((-1)^n*q^(n^2) for n in srange(-11,11)) #\theta_4
###########
##weight-1 cubic theta
###########
#aprim=R((3*q*eta(9)^3+eta(1)^3)/eta(3))
#aa=sum(aprim[3*i]*q^i for i in srange(N/3)) #cubic theta a(\tau), weight 1
##Normalized Eisenstein series
#E2=1-24*sum(n*q^n/(1-q^n) for n in srange(1,20)); #print(E2.O(10))
#E4=240*eisenstein_series_qexp(4,100) #Constant term =1
#E6=-504*eisenstein_series_qexp(6,100)
###########
#Eisenstein series given under the tables on page 53
###########
#E22=E2-2*sum(E2[i]*q^(2*i) for i in srange(20))#E_{2,2} on page 53
#E23=E2-3*sum(E2[i]*q^(3*i) for i in srange(20))#E_{2,3} on page 53

###########
#Period function using Section 4.1 of [Memoirs] based on Jacobi sums
###########
def Jc(a,b,p): #a,b are in ZZ
    D=DirichletGroup(p)
    A1=D[(a)%(p-1)]
    B1=D[(b)%(p-1)]
    return sum(A1(t)*B1(1-t) for t in srange(p))
def BJ(i,j,p):
    G=DirichletGroup(p)
    return -G[j](-1)*Jc(i,(-j)%(p-1),p)
def PP(A,B,lam,p):
    AA=[(a*(p-1))%(p-1) for a in A]
    BB=[(a*(p-1))%(p-1) for a in B]
    n=len(A)
    D=DirichletGroup(p)
    sgn=prod(D[AA[i]](-1)*D[BB[i]](-1) for i in srange(1,n))
    tt=[]
    for i in srange(p-1):
        tt.append( prod(BJ(AA[j]+i,(BB[j]+i)%(p-1),p) for j in srange(n))*D[i](lam))# for i in srange(p-1)]
    return  sum(a for a in tt)*(-1)^(n)/(p-1)*sgn  
##################    
#Given HD^\flat={A,B} and (r,s), (optional, can also be determined internally from HD) modular function t, print HD and q-expansion of f_{HD}
##################

####EHMM has been modified by adding N to indicate how many q-coefficients will be computed
def EHMM(A,B,r,s,N,t=None): #expansion for modular form HD^\flat=\{A,B}, adding r to A, s to B, t is the Hauptmodul
   # N=20
    if t==None:
        for data in HauptTable:
            if [A,B]==data[0]:
                t=data[1]
    if t==None:
        print('Hypergeometric datum does not have corresponding Hauptmodul in Table 1')
        return()
    
    deg=0
    while ((t)[deg]==0): #Locating first leading coefficient exponent
      deg=deg+1
    C=(t)[deg]  #leading coefficient
    M=denominator(deg*(r-1)+1)# M=denominator(deg*r)
    n=numerator(deg*(r-1)+1)# n=numerator(deg*r)
    rmf=(((t/C/q^deg)^(r-1)*(1-t)^(s-r-1)*Hyp(A,B,t,N)*diff(t,q)).O(N)/C/deg) 
    A.append(r)
    B.append(s)
    if M==1:
        return A,B,rmf*q^(deg*(r-1)+1)
    else:    
        tar=sum(rmf[i]*q^(M*i+n) for i in srange(N))
        return 'datum', A,B, 'q-expansion', tar
##################    
#checking condition 2 of Theorem 2.1. If it holds, check (2.12) for the first few primes
##################
def CharTrace(A,B,r,s,t=None):
    if t==None:
        for data in HauptTable:
            if [A,B]==data[0]:
                t=data[1]
    if t==None:
        print('Hypergeometric datum does not have corresponding Hauptmodul in Table 1')
        return()
    ff=EHMM(A,B,r,s,100,t=None);A1=ff[1];B1=ff[2];fHD=ff[4]
    M=lcm(lcm([(a).denominator() for a in A1]),lcm([(a).denominator() for a in B1]))
    ga=sum(b for b in B1)-sum(a for a in A1)-1 #\gamma(\HD)
    C1=t[1]; #leading coeff of t
    L=[['p','MF. pth','noramlized H-values' , 'conclusion']]
    P=[]
    Tr=[]
    for p in primes(10*M):  #can adjust 10 to compute more MF's coefficients
      if p%M==1:
             D=DirichletGroup(p);chi=D[(p-1)*r]
             ss=(-1)^(len(A1)-1)*chi(C1)^(-1)*PP(A1,B1,1,p) # middle term of (2.1) of EHMM
             
             if ss not in ZZ:
                 print('gamma(HD)',ga,'Condition 2 of Theorem 2.1 of [EHMM1] fails') 
                 return ('Try different (r,s) and/or t(q) ')
             else:
                 P.append(p)
                 Tr.append(ss)
                 if ga==1:
                        Z=Zp(p,1)
                        #delta term from (6.3) of EHMM
                        delt=prod([Z(a).gamma() for a in B1])/prod([Z(a).gamma() for a in A1])
                        delt=delt*Z(r).gamma()*Z(s-r).gamma()/Z(s).gamma()*C1^((1-p)*r)
                        if (ZZ(delt%p)-1)==0: #extract the sign of delta
                             delsgn=1
                        if ZZ(delt%p)==p-1:
                            delsgn=-1
                        if (ss-fHD[p])*delsgn==p:
                            L.append([p , fHD[p] ,   ss ,   '(2.12) holds for', p])
                            
                        else:
                            L.append([p , fHD[p] ,  ss ,  '(2.12) fails for',p ])
                            return ('(2.12) of [EHMM1] fails for',p)
                 else:
                   if ss-fHD[p]==0:
                       L.append([p , fHD[p] ,  ss ,   '(2.12) holds for', p])
                   else:  
                        L.append([p , fHD[p] ,  ss ,   '(2.12) fails for', p])
                        return ('(2.12) of [EHMM1] fails for prime',p)
    return 'gamma(HD)',ga, 'Primes checked',P, 'noramlized H-values',Tr, 'passed verification so far', L
###Computing the denominator M(A,B)
def Dem(A,B):
    return lcm(lcm([denominator(c) for c in A]),lcm([denominator(c) for c in B])) 
    
#### Checking whether the (r=1/M,s) expansion is multiplicative for (n,m)=1 where n,m=1 mod M  
#### The algorithm is a brute force search, can be much improved        
def Is_Multiplicative(f,m,k):
    M=f.degree()
    for i in srange(M/m):
        p=i*m+1
        for p1 in srange(2,M/p):
            #p1=j*m+1
            if gcd(p,p1)==1:
                test= f[p*p1]-f[p]*f[p1]
                if abs(test)>0:
                    return "Not Multiplicative", p,p1, f[p*p1],f[p],f[p1]
    for i in srange(M):
        if abs(f[i])>2*p^((k-1)/2):
            return "within", f.degree(), "coeffs. multiplicative  w.r.t. p equiv 1 mod ", m, "Weil bound failed"
    return "within", f.degree(), "coeffs. multiplicative  w.r.t. p equiv 1 mod ", m ,"looks like a weight",k," mod form"
    
########Computing the conjugates (r,s) for K2 in the Galois case

def Conjugate(r,s,M):
    U=[i for i in srange(M) if gcd(i,M)==1]
    Conj=[]
    for c in U:
        rc=fr(r*c)
        sc=fr(s*c)
        if sc>rc:
            Conj.append([rc,sc])
        else:
            Conj.append([rc,sc+1])
    return Conj  

######## Checking whether the Tp candiates among conjugate family are consistent
######## So far only check mf[lc*p]/mf[p] where lc is the leading coefficient and p=1 mod M is a prime
def Is_Galois(A,B,r,s):    
    n=len(A)
    List=[EHMM(A,B,r,s,100)] # Compute input information
    M=Dem(List[0][1],List[0][2]) # Compute denominator
    C=Conjugate(r,s,M)           # Compute conjugates of (r,s)
    for i in srange(1,len(C)):   # add conjugate EHMM to List
        r=C[i][0];s=C[i][1]
        List.append(EHMM([A[i] for i in srange(n)],[B[i] for i in srange(n)],r,s,100))
    P=[]    #compute primes =1 mod M within 100
    for p in primes(100):
        if p%M==1:
            P.append(p)
    Test=[]
    for p in P:  #for each prime in P, compute mf[lc*p]/mf[p] among conjugate family
     Tp=['prime',p,'Tp']  
     tp=[]   
     for list in List:
        mf=list[4]
        lc=0
        while (mf[lc]==0):
            lc=lc+1
        Tp.append(mf[lc*p]/mf[lc])   
        tp.append(mf[lc*p]/mf[lc])
     if Set(tp).cardinality()>1:
         return 'conjugates',C,Test, 'not-Galois' #if more than Tp values disagree, return conclusion
     Test.append(Tp)    
    return 'conjugates',C,Test, 'consistent so far'



In [14]:
EHMM([1/2,1/2],[1,1],1/8,1,8) #only compute 8 coefficients

('datum',
 [1/2, 1/2, 1/8],
 [1, 1, 1],
 'q-expansion',
 q - 3*q^9 - 6*q^17 + 23*q^25 + 12*q^33 - 66*q^41 - 15*q^49 + 84*q^57)

In [32]:
Is_Multiplicative(EHMM([1/2,1/2],[1,1],1/8,1,100)[4],8,3)

('within',
 793,
 'coeffs. multiplicative  w.r.t. p equiv 1 mod ',
 8,
 'looks like a weight',
 3,
 ' mod form')

In [16]:
C=Conjugate(1/8,1,8);print(C)
for c in C:
    print(EHMM([1/2,1/2],[1,1],c[0],c[1],8)[4])

[[1/8, 1], [3/8, 1], [5/8, 1], [7/8, 1]]
q - 3*q^9 - 6*q^17 + 23*q^25 + 12*q^33 - 66*q^41 - 15*q^49 + 84*q^57
q^3 - q^11 - 7*q^19 + 6*q^27 + 16*q^35 - 9*q^43 - 6*q^51 - 9*q^59
q^5 + q^13 - 4*q^21 - 3*q^29 + q^37 - 3*q^45 + 13*q^53 + 13*q^61
q^7 + 3*q^15 + 3*q^23 + 4*q^31 + 3*q^39 - 6*q^47 - 3*q^55 - 3*q^63


In [17]:
Is_Galois([1/2,1/2],[1,1],1/8,1)

('conjugates',
 [[1/8, 1], [3/8, 1], [5/8, 1], [7/8, 1]],
 [['prime', 17, 'Tp', -6, -6, -6, -6],
  ['prime', 41, 'Tp', -66, -66, -66, -66],
  ['prime', 73, 'Tp', -58, -58, -58, -58],
  ['prime', 89, 'Tp', 102, 102, 102, 102],
  ['prime', 97, 'Tp', 26, 26, 26, 26]],
 'consistent so far')

In [20]:
print(EHMM([1/2,1/2],[1,1],1/8,3,10))
CharTrace([1/2,1/2],[1,1],1/8,3)

('datum', [1/2, 1/2, 1/8], [1, 1, 3], 'q-expansion', q - 35*q^9 + 602*q^17 - 6825*q^25 + 57772*q^33 - 392322*q^41 + 2242289*q^49 - 11163724*q^57 + 49670000*q^65 - 201333594*q^73)


('(2.12) of [EHMM1] fails for prime', 17)

In [21]:
print(EHMM([1/2,1/2,1/2],[1,1,1],1/4,3/4,10))
CharTrace([1/2,1/2,1/2],[1,1,1],1/4,3/4)

('datum', [1/2, 1/2, 1/2, 1/4], [1, 1, 1, 3/4], 'q-expansion', q - 10*q^5 + 37*q^9 - 50*q^13 - 30*q^17 + 128*q^21 - 25*q^25 - 34*q^29 - 320*q^33 + 310*q^37)


('gamma(HD)',
 1,
 'Primes checked',
 [5, 13, 17, 29, 37],
 'noramlized H-values',
 [-5, -37, -13, -5, 347],
 'passed verification so far',
 [['p', 'MF. pth', 'noramlized H-values', 'conclusion'],
  [5, -10, -5, '(2.12) holds for', 5],
  [13, -50, -37, '(2.12) holds for', 13],
  [17, -30, -13, '(2.12) holds for', 17],
  [29, -34, -5, '(2.12) holds for', 29],
  [37, 310, 347, '(2.12) holds for', 37]])

In [24]:
print(EHMM([1/2,1/3,2/3],[1,1,1],1/6,2/3,20))
EHMM([1/2,1/6,5/6],[1,1,1],1/3,5/6,20) # The outcome indidate we get holomorphic modular forms which are likely cuspforms, related to the previous one as they
#Their primtive data are the same as the one above. In terms of coefficients, we can see it from some coefficieitns such as 31 and 43 indicating they are both CM and are differed 
#by a cubic twist

('datum', [1/2, 1/3, 2/3, 1/6], [1, 1, 1, 2/3], 'q-expansion', q + 17*q^7 + 89*q^13 + 107*q^19 - 125*q^25 + 308*q^31 - 433*q^37 - 520*q^43 - 54*q^49 - 901*q^61 + 1007*q^67 - 271*q^73 + 503*q^79 + 1513*q^91 + 1853*q^97 - 19*q^103 - 646*q^109)


('datum',
 [1/2, 1/6, 5/6, 1/3],
 [1, 1, 1, 5/6],
 'q-expansion',
 q - 8*q^4 + 20*q^7 - 70*q^13 + 64*q^16 + 56*q^19 - 125*q^25 - 160*q^28 + 308*q^31 + 110*q^37 - 520*q^43 + 57*q^49 + 560*q^52)

In [23]:
EHMM([1/2,1/6,5/6],[1,1,1],1/3,1,20) #When r and s are not chosen suitably, (namely only if we replace 5/6 in the previous
# example by 1, the coefficients grow much faster 

('datum',
 [1/2, 1/6, 5/6, 1/3],
 [1, 1, 1, 1],
 'q-expansion',
 q - 296*q^4 + 9236*q^7 - 13197312*q^10 - 1438765126*q^13 - 1300420949696*q^16 - 390302615218120*q^19 - 204243715293806592*q^22 - 84157588392428150909*q^25 - 40152955563907734312736*q^28 - 18327825236252747470518988*q^31 - 8723444444385825084720463872*q^34 - 4142298035847725949997900246930*q^37 - 1997639005005794062953677592723456*q^40 - 968225226391056059718770965433444872*q^43 - 473113283826873770966848980187323629568*q^46 - 232417271130138849669535565443523635863495*q^49 - 114803435413969085434034249323372053635510032*q^52 - 56962998571953865597881924956564711213678886912*q^55 - 28382072990584135150083709315642491536427140751360*q^58)

In [25]:
EHMM([1/2,1/2],[1,1],1/4,3/4,20) #Theorem 2.4 of EHMM

('datum',
 [1/2, 1/2, 1/4],
 [1, 1, 3/4],
 'q-expansion',
 q + 2*q^5 - 7*q^9 - 14*q^13 + 18*q^17 + 32*q^21 - 21*q^25 - 14*q^29 + 16*q^33 - 30*q^37 - 14*q^41 - 14*q^45 - 15*q^49 + 66*q^53 + 48*q^57 + 82*q^61 - 28*q^65 - 160*q^69 + 66*q^73 - 32*q^77)

In [26]:
[EHMM([1/2,1/2],[1,1],i/8,1,10) for i in [1,3,5,7]] #K2(i/8,1) of EHMM page 18

[('datum',
  [1/2, 1/2, 1/8],
  [1, 1, 1],
  'q-expansion',
  q - 3*q^9 - 6*q^17 + 23*q^25 + 12*q^33 - 66*q^41 - 15*q^49 + 84*q^57 + 48*q^65 - 58*q^73),
 ('datum',
  [1/2, 1/2, 3/8],
  [1, 1, 1],
  'q-expansion',
  q^3 - q^11 - 7*q^19 + 6*q^27 + 16*q^35 - 9*q^43 - 6*q^51 - 9*q^59 - 23*q^67 + 23*q^75),
 ('datum',
  [1/2, 1/2, 5/8],
  [1, 1, 1],
  'q-expansion',
  q^5 + q^13 - 4*q^21 - 3*q^29 + q^37 - 3*q^45 + 13*q^53 + 13*q^61 - 12*q^69 + 4*q^77),
 ('datum',
  [1/2, 1/2, 7/8],
  [1, 1, 1],
  'q-expansion',
  q^7 + 3*q^15 + 3*q^23 + 4*q^31 + 3*q^39 - 6*q^47 - 3*q^55 - 3*q^63 - 15*q^71 - 2*q^79)]

In [27]:
CharTrace([1/2,1/2],[1,1],1/2,1)

('gamma(HD)',
 1/2,
 'Primes checked',
 [3, 5, 7, 11, 13, 17, 19],
 'noramlized H-values',
 [0, -6, 0, 0, 10, -30, 0],
 'passed verification so far',
 [['p', 'MF. pth', 'noramlized H-values', 'conclusion'],
  [3, 0, 0, '(2.12) holds for', 3],
  [5, -6, -6, '(2.12) holds for', 5],
  [7, 0, 0, '(2.12) holds for', 7],
  [11, 0, 0, '(2.12) holds for', 11],
  [13, 10, 10, '(2.12) holds for', 13],
  [17, -30, -30, '(2.12) holds for', 17],
  [19, 0, 0, '(2.12) holds for', 19]])

In [28]:
CharTrace([1/2,1/2,1/2],[1,1,1],1/12,1/12+1/2)

('gamma(HD)',
 1,
 'Primes checked',
 [13, 37, 61, 73, 97, 109],
 'noramlized H-values',
 [-1, -229, -485, 703, 1679, -225],
 'passed verification so far',
 [['p', 'MF. pth', 'noramlized H-values', 'conclusion'],
  [13, -14, -1, '(2.12) holds for', 13],
  [37, -266, -229, '(2.12) holds for', 37],
  [61, -546, -485, '(2.12) holds for', 61],
  [73, 630, 703, '(2.12) holds for', 73],
  [97, 1582, 1679, '(2.12) holds for', 97],
  [109, -334, -225, '(2.12) holds for', 109]])

In [30]:
CharTrace([1/2,1/3,2/3],[1,1,1],1/6,2/3)

gamma(HD) 1 Condition 2 of Theorem 2.1 of [EHMM1] fails


'Try different (r,s) and/or t(q) '

In [31]:
CharTrace([1/2,1/2,1/2],[1,1,1],1/24,1/24+1/2)

('gamma(HD)',
 1,
 'Primes checked',
 [73, 97, 193],
 'noramlized H-values',
 [-423, 673, 4037],
 'passed verification so far',
 [['p', 'MF. pth', 'noramlized H-values', 'conclusion'],
  [73, -350, -423, '(2.12) holds for', 73],
  [97, 770, 673, '(2.12) holds for', 97],
  [193, 4230, 4037, '(2.12) holds for', 193]])